# Анализ пространственных данных. Домашнее задание №2

Мягкий дедлайн: __4 ноября 2020 г. 23:59__

Жесткий дедлайн (со штрафом в _50%_ от количества набранных вами за ДЗ баллов): __5 ноября 2020 г. 08:59__

Визуализация "чего-либо" __без__ выполненного основного задания оценивается в __0 баллов__

ФИО: `Фомин Фёдор Васильевич`

Группа: `MADE-DS-11`

## Задание №1. Горячая точка (алгоритм - 10 баллов, визуализация - 10 баллов).

Генерируйте рандомные точки на планете Земля до тех пор, пока не попадете на территорию ``Афганистана``

1. Вы можете использовать функции принадлжености точки полигону и расстояния от точки до полигона (в метрах)
2. Предложите не наивный алгоритм поиска (генерировать __напрямую__ точку из полигона границ Афганистана __запрещено__)

In [59]:
import folium
import random

from OSMPythonTools.overpass import Overpass
from shapely.geometry import Point, Polygon, LineString

# создаём полигон Афганистана
overpass = Overpass()
result = overpass.query('''
                        area["ISO3166-1"="AF"][admin_level=2];
                        relation["boundary"="administrative"](area);
                        out geom;
                        ''')
poly_afgan = Polygon(result.elements()[0].geometry()['coordinates'][0])

# создаём полигон Земли
poly_earth = Polygon([[-180, 90], [-180, -90], [180, -90], [180, 90]])

In [60]:
# функция рандомного взятия точки из полигона
def random_point_within(poly):
    min_x, min_y, max_x, max_y = poly.bounds
    random_point = Point([random.uniform(min_x, max_x), random.uniform(min_y, max_y)])
    return random_point

In [67]:
# создаём карту folium
m = folium.Map(
    location=[-59.1759, -11.6016],
    zoom_start=1  # Limited levels of zoom for free Mapbox tiles.
)

# создаём список случайных точек
points = []
poly_current = poly_earth

# случайно выбираем первую точку
random_point = random_point_within(poly_current)
points.append(random_point)
i = 1

# ставим маркер стартовой (первой) точки на карту
folium.Marker(
                location=(random_point.coords[0][1], random_point.coords[0][0]),
                icon=folium.Icon(color="green", icon="heart", prefix='fa') 
).add_to(m)

# добавляем текст на маркер
folium.Marker(
                location=(random_point.coords[0][1], random_point.coords[0][0]),
                icon=folium.features.DivIcon(icon_anchor=(5, 20),
                                            html='<div style="font-size: 8pt">'+ str(i) + '</div>')
            ).add_to(m)

while random_point.within(poly_afgan) != True:
    i += 1
    
# смотрим пересечение между полигоном, с которого выбиралась точка, и полигоном, который образаует эта точка
    poly_current = random_point.buffer(poly_afgan.centroid.distance(random_point.centroid) + 10).intersection(poly_current)
    random_point = random_point_within(poly_current)
    points.append(random_point)

# добавляем маркер случайной точки
    folium.Marker(
                location=(random_point.coords[0][1], random_point.coords[0][0]),
                icon=folium.Icon(color="red", icon="heart", prefix='fa') 
                ).add_to(m)

# добавляем текст на маркер
    folium.Marker(
                location=(random_point.coords[0][1], random_point.coords[0][0]),
                icon=folium.features.DivIcon(icon_anchor=(5, 20),
                                                html='<div style="font-size: 8pt">'+ str(i) + '</div>')
                ).add_to(m)

# создаём линию из точек
line = LineString(points)

# добавляем на карту полигон Афганистана
folium.GeoJson(
    poly_afgan
).add_to(m)

# добавляем на карту пуnm от первой до последней точки
folium.GeoJson(
    line
).add_to(m)

m

Визуализируйте пошагово предложенный алгоритм при помощи ``Folium``

## Задание №2. Качество жизни (20 баллов).

Для измерения показателя качества жизни в точке, найденной в предыдущем задании, вам необходимо рассчитать следующую сумму расстояний (в метрах):

1. Расстояние от точки до 5 ближайших __*__ банкоматов, находящихся в стране с наибольшим количеством объектов жилой недвижимости
2. Расстояние от точки до 5 ближайших школ, находящихся в стране с наибольшим количеством аптек в столице
3. Расстояние от точки до 5 ближайших кинотеатров, наодящихся в стране с самым большим отношением числа железнодорожных станций к автобусным остановкам в южной части __**__

__*__ При поиске _N_ ближайших объектов обязательно использовать ``R-tree``

__**__ Южной частью страны является территория, находящаяся к югу от множества точек, равноудаленных от самой северной и самой южной точек страны

In [ ]:
# put your code here

## Задание №3. Поездка по Нью-Йорку (маршрут - 20 баллов, визуализация - 10 баллов).

Добраться __на автомобиле__ от входа в ``Central Park`` __Нью-Йорка__ (со стороны ``5th Avenue``) до пересечения ``Water Street`` и ``Washington Street`` в Бруклине (откуда получаются лучшие фото Манхэттенского моста) довольно непросто - разумеется, из-за вечных пробок. Однако еще сложнее это сделать, проезжая мимо школ, где дети то и дело переходят дорогу в неположенном месте.

Вам необходимо построить описанный выше маршрут, избегая на своем пути школы. Визуализируйте данный маршрут (также добавив школы и недоступные для проезда участки дорог) при помощи ``Folium``

Данные о расположении школ Нью-Йорка можно найти [здесь](https://catalog.data.gov/dataset/2019-2020-school-point-locations)

In [ ]:
# put your code here

In [68]:
import pandas as pd

from shapely import wkt
from shapely.geometry import shape, Polygon, mapping, MultiPolygon, LineString, Point
from shapely.ops import cascaded_union

import folium
from folium import Map, Marker, LayerControl
from openrouteservice import client

from shapely import geometry
from shapely.ops import cascaded_union, transform

import pyproj

In [69]:
# загружаем адреса школ
schools_df = pd.read_csv('2019_-_2020_School_Point_Locations.csv')
school_points = schools_df['the_geom'].apply(lambda x: wkt.loads(x))

In [70]:
# функция для перевода координат
def transform_for_buffer(point, distance, resolution):
    wgs84_pt = point

    wgs84 = pyproj.CRS('EPSG:4326')
    utm = pyproj.CRS('EPSG:32632')

    project = pyproj.Transformer.from_crs(wgs84, utm, always_xy=True).transform
    utm_point = transform(project, wgs84_pt)
    utm_point_buffer = Point(utm_point).buffer(distance=distance, resolution=resolution)


    poly_wgs = []

    project = pyproj.Transformer.from_crs(utm, wgs84, always_xy=True).transform

    for point in utm_point_buffer.exterior.coords:
        poly_wgs.append(transform(project, Point(point)))

    return poly_wgs 

In [71]:
# строим карту
m = folium.Map(
    location=[40.76510, -73.97317],
    zoom_start=14
)

# координаты начала и конца пути
coordinates = [[40.76510, -73.97317], [40.70316353, -73.98958862]] # Central Park and Water-Washington Street
for coord in coordinates:
    folium.Marker(coord).add_to(m)
coordinates = [[-73.97317, 40.76510], [-73.98958862, 40.70316353]]


list_school_poly_coord = [] # лист с координатами полигонов школ
list_school_poly_geom = [] # лист с полигонами школ

for point in school_points:
    folium.CircleMarker(location=(point.coords[0][1], point.coords[0][0]), 
                        color='red',
                        radius=1,
                        weight=2).add_to(m)
    
    school_poly_coord = transform_for_buffer(point, resolution=2, distance=100)
    list_school_poly_coord.append(school_poly_coord)
    poly = Polygon(school_poly_coord)  
    list_school_poly_geom.append(poly)
    
union_poly = mapping(cascaded_union(list_school_poly_geom))
folium.GeoJson(data=union_poly,
               name='Schools Poly').add_to(m)

m

In [72]:
from openrouteservice import client
api_key = '5b3ce3597851110001cf62481dc9cc0566844b01abacf1cc40f6bb33' 
clnt = client.Client(key=api_key)

In [73]:
def style_function(color): # To style data
    return lambda feature: dict(color=color)

In [74]:
# Regular Route
route_request = {'coordinates': coordinates, 
                'format_out': 'geojson',
                'profile': 'driving-car',
                'preference': 'shortest',
                'instructions': False
                }
route_directions = clnt.directions(**route_request)

folium.GeoJson(data=route_directions,
                        name='Regular Route',
                        style_function=style_function('#ff5050'),
                        overlay=True).add_to(m)

In [75]:
# Route WITHOUT schools
route_request = {'coordinates': coordinates, 
                    'format_out': 'geojson',
                    'profile': 'driving-car',
                    'preference': 'shortest',
                    'instructions': False,
                    'options': {'avoid_polygons': union_poly}}
route_directions = clnt.directions(**route_request)

folium.GeoJson(data=route_directions,
                name='Route WITHOUT schools',
                style_function=style_function('#006600'),
            overlay=True).add_to(m)

In [76]:
m.add_child(folium.map.LayerControl())
m